## Applied Data Science Capstone Week 4

In [1]:
import numpy as np
import pandas as pd
from bs4 import BeautifulSoup
from urllib.request import urlopen
import requests

### Web Scraping Wikipedia Table using BeautifulSoup and Python  
reference: https://medium.com/analytics-vidhya/web-scraping-wiki-tables-using-beautifulsoup-and-python-6b9ea26d8722

In [2]:
page = urlopen('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').read().decode()
soup = BeautifulSoup(page, 'html.parser')

In [3]:
table = soup.find('table', class_='wikitable')
rows = table.find_all('tr')

In [4]:
data = []
for row in rows:
    data.append(row.text.split('\n')[1:-1])

In [5]:
df = pd.DataFrame(data[1:], columns = data[0])
df.head(20)

Postcode           Borough     Neighbourhood
0       M1A      Not assigned      Not assigned
1       M2A      Not assigned      Not assigned
2       M3A        North York         Parkwoods
3       M4A        North York  Victoria Village
4       M5A  Downtown Toronto      Harbourfront
5       M5A  Downtown Toronto       Regent Park
6       M6A        North York  Lawrence Heights
7       M6A        North York    Lawrence Manor
8       M7A      Queen's Park      Not assigned
9       M8A      Not assigned      Not assigned
10      M9A         Etobicoke  Islington Avenue
11      M1B       Scarborough             Rouge
12      M1B       Scarborough           Malvern
13      M2B      Not assigned      Not assigned
14      M3B        North York   Don Mills North
15      M4B         East York  Woodbine Gardens
16      M4B         East York     Parkview Hill
17      M5B  Downtown Toronto           Ryerson
18      M5B  Downtown Toronto   Garden District
19      M6B        North York         Glencairn

### Only process the cells that have an assigned borough. Ignore cells with a borough that is Not assigned.

In [6]:
df1 = df[df.Borough != 'Not assigned']
df1.reset_index(drop=True, inplace=True)
df1.head(20)

Postcode           Borough     Neighbourhood
0       M3A        North York         Parkwoods
1       M4A        North York  Victoria Village
2       M5A  Downtown Toronto      Harbourfront
3       M5A  Downtown Toronto       Regent Park
4       M6A        North York  Lawrence Heights
5       M6A        North York    Lawrence Manor
6       M7A      Queen's Park      Not assigned
7       M9A         Etobicoke  Islington Avenue
8       M1B       Scarborough             Rouge
9       M1B       Scarborough           Malvern
10      M3B        North York   Don Mills North
11      M4B         East York  Woodbine Gardens
12      M4B         East York     Parkview Hill
13      M5B  Downtown Toronto           Ryerson
14      M5B  Downtown Toronto   Garden District
15      M6B        North York         Glencairn
16      M9B         Etobicoke        Cloverdale
17      M9B         Etobicoke         Islington
18      M9B         Etobicoke      Martin Grove
19      M9B         Etobicoke  Princess Gardens

### Group by postcode and borough to remove duplicates, at the same time join neighborhoods using comma
* More than one neighborhood can exist in one postal code area. For example, in the table on the Wikipedia page, you will notice that M5A is listed twice and has two neighborhoods: Harbourfront and Regent Park. These two rows will be combined into one row with the neighborhoods separated with a comma as shown in row 11 in the above table.
* If a cell has a borough but a Not assigned neighborhood, then the neighborhood will be the same as the borough. So for the 9th cell in the table on the Wikipedia page, the value of the Borough and the Neighborhood columns will be Queen's Park.

In [7]:
df1 = df1.groupby(['Postcode', 'Borough'])['Neighbourhood'].apply(', '.join).reset_index()

In [8]:
df1.loc[df1.Neighbourhood == 'Not assigned', 'Neighbourhood'] = df1[df1.Neighbourhood == 'Not assigned']['Borough']
df1.head(20)

Postcode      Borough                                      Neighbourhood
0       M1B  Scarborough                                     Rouge, Malvern
1       M1C  Scarborough             Highland Creek, Rouge Hill, Port Union
2       M1E  Scarborough                  Guildwood, Morningside, West Hill
3       M1G  Scarborough                                             Woburn
4       M1H  Scarborough                                          Cedarbrae
5       M1J  Scarborough                                Scarborough Village
6       M1K  Scarborough        East Birchmount Park, Ionview, Kennedy Park
7       M1L  Scarborough                    Clairlea, Golden Mile, Oakridge
8       M1M  Scarborough    Cliffcrest, Cliffside, Scarborough Village West
9       M1N  Scarborough                        Birch Cliff, Cliffside West
10      M1P  Scarborough  Dorset Park, Scarborough Town Centre, Wexford ...
11      M1R  Scarborough                                  Maryvale, Wexford
12      M1S  Scarborough                                          Agincourt
13      M1T  Scarborough            Clarks Corners, Sullivan, Tam O'Shanter
14      M1V  Scarborough  Agincourt North, L'Amoreaux East, Milliken, St...
15      M1W  Scarborough                                    L'Amoreaux West
16      M1X  Scarborough                                        Upper Rouge
17      M2H   North York                                  Hillcrest Village
18      M2J   North York                       Fairview, Henry Farm, Oriole
19      M2K   North York                                    Bayview Village

###  Use the .shape method to print the number of rows of your dataframe.

In [9]:
print('Shape of result',df1.shape)

Shape of result (103, 3)


### Create dataframe with the latitude and the longitude 
here I just used the csv data provided, the join two tables on postcode

In [10]:
geodata = pd.read_csv('http://cocl.us/Geospatial_data')
geodata.rename(columns={'Postal Code':'Postcode'}, inplace=True)
geodata.head(10)

Postcode   Latitude  Longitude
0      M1B  43.806686 -79.194353
1      M1C  43.784535 -79.160497
2      M1E  43.763573 -79.188711
3      M1G  43.770992 -79.216917
4      M1H  43.773136 -79.239476
5      M1J  43.744734 -79.239476
6      M1K  43.727929 -79.262029
7      M1L  43.711112 -79.284577
8      M1M  43.716316 -79.239476
9      M1N  43.692657 -79.264848

In [11]:
df2 = df1.merge(geodata, on = 'Postcode')
df2.head(20)

Postcode      Borough                                      Neighbourhood  \
0       M1B  Scarborough                                     Rouge, Malvern   
1       M1C  Scarborough             Highland Creek, Rouge Hill, Port Union   
2       M1E  Scarborough                  Guildwood, Morningside, West Hill   
3       M1G  Scarborough                                             Woburn   
4       M1H  Scarborough                                          Cedarbrae   
5       M1J  Scarborough                                Scarborough Village   
6       M1K  Scarborough        East Birchmount Park, Ionview, Kennedy Park   
7       M1L  Scarborough                    Clairlea, Golden Mile, Oakridge   
8       M1M  Scarborough    Cliffcrest, Cliffside, Scarborough Village West   
9       M1N  Scarborough                        Birch Cliff, Cliffside West   
10      M1P  Scarborough  Dorset Park, Scarborough Town Centre, Wexford ...   
11      M1R  Scarborough                                  Maryvale, Wexford   
12      M1S  Scarborough                                          Agincourt   
13      M1T  Scarborough            Clarks Corners, Sullivan, Tam O'Shanter   
14      M1V  Scarborough  Agincourt North, L'Amoreaux East, Milliken, St...   
15      M1W  Scarborough                                    L'Amoreaux West   
16      M1X  Scarborough                                        Upper Rouge   
17      M2H   North York                                  Hillcrest Village   
18      M2J   North York                       Fairview, Henry Farm, Oriole   
19      M2K   North York                                    Bayview Village   

     Latitude  Longitude  
0   43.806686 -79.194353  
1   43.784535 -79.160497  
2   43.763573 -79.188711  
3   43.770992 -79.216917  
4   43.773136 -79.239476  
5   43.744734 -79.239476  
6   43.727929 -79.262029  
7   43.711112 -79.284577  
8   43.716316 -79.239476  
9   43.692657 -79.264848  
10  43.757410 -79.273304  
11  43.750072 -79.295849  
12  43.794200 -79.262029  
13  43.781638 -79.304302  
14  43.815252 -79.284577  
15  43.799525 -79.318389  
16  43.836125 -79.205636  
17  43.803762 -79.363452  
18  43.778517 -79.346556  
19  43.786947 -79.385975

### Cluster the neighborhoods in Toronto
I just worked with only boroughs that contain the word Toronto 

In [12]:
df3 = df2[df2.Borough.str.contains("Toronto")]
df3.head(20)

Postcode           Borough  \
37      M4E      East Toronto   
41      M4K      East Toronto   
42      M4L      East Toronto   
43      M4M      East Toronto   
44      M4N   Central Toronto   
45      M4P   Central Toronto   
46      M4R   Central Toronto   
47      M4S   Central Toronto   
48      M4T   Central Toronto   
49      M4V   Central Toronto   
50      M4W  Downtown Toronto   
51      M4X  Downtown Toronto   
52      M4Y  Downtown Toronto   
53      M5A  Downtown Toronto   
54      M5B  Downtown Toronto   
55      M5C  Downtown Toronto   
56      M5E  Downtown Toronto   
57      M5G  Downtown Toronto   
58      M5H  Downtown Toronto   
59      M5J  Downtown Toronto   

                                        Neighbourhood   Latitude  Longitude  
37                                        The Beaches  43.676357 -79.293031  
41                       The Danforth West, Riverdale  43.679557 -79.352188  
42                     The Beaches West, India Bazaar  43.668999 -79.315572  
43                                    Studio District  43.659526 -79.340923  
44                                      Lawrence Park  43.728020 -79.388790  
45                                   Davisville North  43.712751 -79.390197  
46                                 North Toronto West  43.715383 -79.405678  
47                                         Davisville  43.704324 -79.388790  
48                        Moore Park, Summerhill East  43.689574 -79.383160  
49  Deer Park, Forest Hill SE, Rathnelly, South Hi...  43.686412 -79.400049  
50                                           Rosedale  43.679563 -79.377529  
51                        Cabbagetown, St. James Town  43.667967 -79.367675  
52                               Church and Wellesley  43.665860 -79.383160  
53                          Harbourfront, Regent Park  43.654260 -79.360636  
54                           Ryerson, Garden District  43.657162 -79.378937  
55                                     St. James Town  43.651494 -79.375418  
56                                        Berczy Park  43.644771 -79.373306  
57                                 Central Bay Street  43.657952 -79.387383  
58                           Adelaide, King, Richmond  43.650571 -79.384568  
59  Harbourfront East, Toronto Islands, Union Station  43.640816 -79.381752

In [13]:
from sklearn.cluster import KMeans
#!conda install -c conda-forge folium=0.5.0 --yes
import folium

#### K-means clustering and visualization,
Reference: Week3 Lab - Segmenting and Clustering Neighborhoods in New York City

In [14]:
# set number of clusters = 5
kclusters = 5
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(df3[['Latitude', 'Longitude']])

In [15]:
df3['Cluster Labels']=kmeans.labels_
df3.head(20)

/Users/chenfeiwang/anaconda/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


Postcode           Borough  \
37      M4E      East Toronto   
41      M4K      East Toronto   
42      M4L      East Toronto   
43      M4M      East Toronto   
44      M4N   Central Toronto   
45      M4P   Central Toronto   
46      M4R   Central Toronto   
47      M4S   Central Toronto   
48      M4T   Central Toronto   
49      M4V   Central Toronto   
50      M4W  Downtown Toronto   
51      M4X  Downtown Toronto   
52      M4Y  Downtown Toronto   
53      M5A  Downtown Toronto   
54      M5B  Downtown Toronto   
55      M5C  Downtown Toronto   
56      M5E  Downtown Toronto   
57      M5G  Downtown Toronto   
58      M5H  Downtown Toronto   
59      M5J  Downtown Toronto   

                                        Neighbourhood   Latitude  Longitude  \
37                                        The Beaches  43.676357 -79.293031   
41                       The Danforth West, Riverdale  43.679557 -79.352188   
42                     The Beaches West, India Bazaar  43.668999 -79.315572   
43                                    Studio District  43.659526 -79.340923   
44                                      Lawrence Park  43.728020 -79.388790   
45                                   Davisville North  43.712751 -79.390197   
46                                 North Toronto West  43.715383 -79.405678   
47                                         Davisville  43.704324 -79.388790   
48                        Moore Park, Summerhill East  43.689574 -79.383160   
49  Deer Park, Forest Hill SE, Rathnelly, South Hi...  43.686412 -79.400049   
50                                           Rosedale  43.679563 -79.377529   
51                        Cabbagetown, St. James Town  43.667967 -79.367675   
52                               Church and Wellesley  43.665860 -79.383160   
53                          Harbourfront, Regent Park  43.654260 -79.360636   
54                           Ryerson, Garden District  43.657162 -79.378937   
55                                     St. James Town  43.651494 -79.375418   
56                                        Berczy Park  43.644771 -79.373306   
57                                 Central Bay Street  43.657952 -79.387383   
58                           Adelaide, King, Richmond  43.650571 -79.384568   
59  Harbourfront East, Toronto Islands, Union Station  43.640816 -79.381752   

    Cluster Labels  
37               3  
41               3  
42               3  
43               3  
44               1  
45               1  
46               1  
47               1  
48               1  
49               1  
50               2  
51               2  
52               2  
53               2  
54               2  
55               2  
56               2  
57               2  
58               2  
59               2

In [16]:
import matplotlib.cm as cm
import matplotlib.colors as colors

# create map
map_clusters = folium.Map(location=[43.65, -79.4], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(df3['Latitude'], df3['Longitude'], df3['Neighbourhood'], df3['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color='black',
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [17]:
# get nearby venues function
def getNearbyVenues(areas, latitudes, longitudes, radius=5000, categoryIds=''):

    venues_list=[]
    for area, lat, lng in zip(areas, latitudes, longitudes):

        # API request URL
        url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, VERSION, lat, lng, radius, limit)
        
        if (categoryIds != ''):
            url = url + '&categoryId={}'
            url = url.format(categoryIds)

        # GET request
        response = requests.get(url).json()
        results = response["response"]['venues']

        # get data from json
        for v in results:
            success = False
            try:
                category = v['categories'][0]['name']
                success = True
            except:
                pass

            if success:
                venues_list.append([(area, lat, lng, v['name'], v['location']['lat'], v['location']['lng'],v['categories'][0]['name'])])
        #break

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Area', 'Area Latitude', 'Area Longitude', 'Venue', 'Venue Latitude', 'Venue Longitude', 'Venue Category']

    return(nearby_venues)

# function plot venues on map
def plotVenue(df, color, existingMap):
    for lat, lng, local, venue, venueCat in zip(df['Venue Latitude'], df['Venue Longitude'], df['Area'], df['Venue'], df['Venue Category']):
        label = '{} ({}) - {}'.format(venue, venueCat, local)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.7).add_to(existingMap)
        
# function to append column of venue counts
def addCol(base, coltitle, venues):
    grouped = venues.Area.value_counts()
    
    for n in base['Postcode']:
        try:
            base.loc[base['Postcode'] == n,coltitle] = grouped.loc[n]
        except:
            base.loc[base['Postcode'] == n,coltitle] = 0

In [18]:
limit = 500
CLIENT_ID = 'XFHY3G2CF1GI2JS4SNUXMDLBMILWUQXBICCIRRASMKCCQFTE'
CLIENT_SECRET = 'PFDP2UTAKZF0JG5JQCHFU2VCQJ3VN3SL0NQUTZ3RVFHD3AMV'
VERSION = '20190409'

In [19]:
# get fast food chains
fast_food = getNearbyVenues(areas=df3['Postcode'], latitudes=df3['Latitude'], longitudes=df3['Longitude'], radius=1000, categoryIds='4bf58dd8d48988d16e941735')
print(fast_food.shape)
fast_food.head()

(873, 7)


Area  Area Latitude  Area Longitude   Venue  Venue Latitude  \
0  M4E      43.676357      -79.293031  Subway       43.671013   
1  M4E      43.676357      -79.293031  Subway       43.680668   
2  M4K      43.679557      -79.352188  Subway       43.676867   
3  M4K      43.679557      -79.352188     A&W       43.677537   
4  M4K      43.679557      -79.352188  Subway       43.677536   

   Venue Longitude        Venue Category  
0       -79.295512        Sandwich Place  
1       -79.287090        Sandwich Place  
2       -79.355546        Sandwich Place  
3       -79.351459  Fast Food Restaurant  
4       -79.357333        Sandwich Place

In [20]:
fast_food_map = folium.Map(location=[43.65, -79.4], zoom_start=12)
plotVenue(fast_food, 'red', fast_food_map)
fast_food_map

In [21]:
# get schools
school = getNearbyVenues(areas=df3['Postcode'], latitudes=df3['Latitude'], longitudes=df3['Longitude'], radius=1000, categoryIds='4bf58dd8d48988d13d941735')
print(school.shape)
school.head()

(188, 7)


Area  Area Latitude  Area Longitude                             Venue  \
0  M4E      43.676357      -79.293031                Malvern Collegiate   
1  M4E      43.676357      -79.293031  Neil McNeil Catholic High School   
2  M4K      43.679557      -79.352188                  Montcrest School   
3  M4K      43.679557      -79.352188              Degrassi High School   
4  M4K      43.679557      -79.352188        City Adult Learning Centre   

   Venue Latitude  Venue Longitude Venue Category  
0       43.683360       -79.293039    High School  
1       43.679723       -79.283146    High School  
2       43.673748       -79.356864    High School  
3       43.684306       -79.349092    High School  
4       43.675408       -79.359885    High School

In [22]:
school_map = folium.Map(location=[43.65, -79.4], zoom_start=12)
plotVenue(school, 'green', school_map)
school_map

In [23]:
# get universities
university = getNearbyVenues(areas=df3['Postcode'], latitudes=df3['Latitude'], longitudes=df3['Longitude'], radius=1000, categoryIds='4bf58dd8d48988d1a8941735')
print(university.shape)
university.head()

(421, 7)


Area  Area Latitude  Area Longitude                             Venue  \
0  M4E      43.676357      -79.293031           Glen Ames Swimming Pool   
1  M4L      43.668999      -79.315572           Le Petit Chaperon Rouge   
2  M4M      43.659526      -79.340923  Leslieville Junior Public School   
3  M4N      43.728020      -79.388790           Glendon Smokers' Corner   
4  M4N      43.728020      -79.388790                   Glendon Gallery   

   Venue Latitude  Venue Longitude                Venue Category  
0       43.674623       -79.298152  General College & University  
1       43.677554       -79.320407  General College & University  
2       43.666730       -79.331884  General College & University  
3       43.727348       -79.378467  General College & University  
4       43.727256       -79.378725                   Art Gallery

In [24]:
uni_map = folium.Map(location=[43.65, -79.4], zoom_start=12)
plotVenue(university, 'blue', uni_map)
uni_map

In [25]:
# get offices
office = getNearbyVenues(areas=df3['Postcode'], latitudes=df3['Latitude'], longitudes=df3['Longitude'], radius=1000, categoryIds='4bf58dd8d48988d124941735')
print(office.shape)
office.head()

(1629, 7)


Area  Area Latitude  Area Longitude                        Venue  \
0  M4E      43.676357      -79.293031          dashwood & dashwood   
1  M4E      43.676357      -79.293031            Barrett And Welsh   
2  M4E      43.676357      -79.293031  Kate Britain Marketing Inc.   
3  M4E      43.676357      -79.293031             The Donnee Group   
4  M4E      43.676357      -79.293031                    TwoPointO   

   Venue Latitude  Venue Longitude Venue Category  
0       43.680506       -79.287227         Office  
1       43.678460       -79.299442         Office  
2       43.668612       -79.294477         Office  
3       43.682732       -79.290801         Office  
4       43.678487       -79.299402         Office

In [26]:
office_map = folium.Map(location=[43.65, -79.4], zoom_start=12)
plotVenue(office, 'gold', office_map)
office_map

In [27]:
#append the counts of venues for each area
df4 = df3.copy()
addCol(df4, 'Fast Food Restaurants', fast_food)
addCol(df4, 'High Schools', school)
addCol(df4, 'Universities', university)
addCol(df4, 'Offices', office)
df4.head()

Postcode          Borough                   Neighbourhood   Latitude  \
37      M4E     East Toronto                     The Beaches  43.676357   
41      M4K     East Toronto    The Danforth West, Riverdale  43.679557   
42      M4L     East Toronto  The Beaches West, India Bazaar  43.668999   
43      M4M     East Toronto                 Studio District  43.659526   
44      M4N  Central Toronto                   Lawrence Park  43.728020   

    Longitude  Cluster Labels  Fast Food Restaurants  High Schools  \
37 -79.293031               3                    2.0           2.0   
41 -79.352188               3                   13.0           4.0   
42 -79.315572               3                    7.0           0.0   
43 -79.340923               3                    7.0           2.0   
44 -79.388790               1                    4.0           5.0   

    Universities  Offices  
37           1.0     31.0  
41           0.0     41.0  
42           1.0     30.0  
43           1.0     47.0  
44           2.0     11.0

In [28]:
# give fast food restaurant a negative weight and schools/offices a positive wight and calculate the scores
df4['Score'] = df4['Fast Food Restaurants'] * -2 + df4['High Schools'] * 1 + df4['Universities'] * 2 + df4['Offices'] * 2
df4 = df4.sort_values(by=['Score'], ascending=False)
df4.head()

Postcode           Borough                        Neighbourhood   Latitude  \
52      M4Y  Downtown Toronto                 Church and Wellesley  43.665860   
66      M5S  Downtown Toronto       Harbord, University of Toronto  43.662696   
57      M5G  Downtown Toronto                   Central Bay Street  43.657952   
65      M5R   Central Toronto  The Annex, North Midtown, Yorkville  43.672710   
47      M4S   Central Toronto                           Davisville  43.704324   

    Longitude  Cluster Labels  Fast Food Restaurants  High Schools  \
52 -79.383160               2                   48.0          12.0   
66 -79.400049               0                   44.0          11.0   
57 -79.387383               2                   50.0          13.0   
65 -79.405678               0                   24.0           7.0   
47 -79.388790               1                   17.0           6.0   

    Universities  Offices  Score  
52          47.0     50.0  110.0  
66          43.0     49.0  107.0  
57          45.0     50.0  103.0  
65          25.0     47.0  103.0  
47          15.0     47.0   96.0

In [34]:
df4[['Postcode', 'Neighbourhood', 'Fast Food Restaurants', 'High Schools', 'Universities', 'Offices', 'Score']].head(10)

Postcode                                      Neighbourhood  \
52      M4Y                               Church and Wellesley   
66      M5S                     Harbord, University of Toronto   
57      M5G                                 Central Bay Street   
65      M5R                The Annex, North Midtown, Yorkville   
47      M4S                                         Davisville   
45      M4P                                   Davisville North   
50      M4W                                           Rosedale   
51      M4X                        Cabbagetown, St. James Town   
49      M4V  Deer Park, Forest Hill SE, Rathnelly, South Hi...   
46      M4R                                 North Toronto West   

    Fast Food Restaurants  High Schools  Universities  Offices  Score  
52                   48.0          12.0          47.0     50.0  110.0  
66                   44.0          11.0          43.0     49.0  107.0  
57                   50.0          13.0          45.0     50.0  103.0  
65                   24.0           7.0          25.0     47.0  103.0  
47                   17.0           6.0          15.0     47.0   96.0  
45                   15.0           5.0          12.0     46.0   91.0  
50                    9.0           2.0           4.0     49.0   90.0  
51                   14.0           9.0           9.0     45.0   89.0  
49                    9.0           3.0           3.0     48.0   87.0  
46                    9.0          10.0           6.0     41.0   86.0

In [29]:
# plot all the areas, darker color means better place to open new fast food resttaurant

def get_color(x):
    n = int(x // 13)
    color = ["#FFEDA0", "#FED976", "#FEB24C", "#FD8D3C", "#FC4E2A", "#E31A1C", "#E31A1C", "#BD0026", "#800026" ]
    return color[n]
   
overview = folium.Map(location=[43.65, -79.4], zoom_start=12)

for lat, lng, local, score in zip(df4['Latitude'], df4['Longitude'], df4['Postcode'], df4['Score']):
    label = '{}'.format(local)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=10,
        popup=label,
        color=get_color(score),
        fill=True,
        fill_color=get_color(score),
        fill_opacity=0.7).add_to(overview)
        
overview

In [32]:
# Take a closer look at the best area selected

best = df4.head(1)
best_area = folium.Map(location=[best.iloc[0]['Latitude'], best.iloc[0]['Longitude']], zoom_start=15)

plotVenue(fast_food[fast_food['Area'] == best.iloc[0]['Postcode']], 'red', best_area)
plotVenue(school[school['Area'] == best.iloc[0]['Postcode']], 'green', best_area)
plotVenue(university[university['Area'] == best.iloc[0]['Postcode']], 'blue', best_area)
plotVenue(office[office['Area'] == best.iloc[0]['Postcode']], 'gold', best_area)

best_area

### CAPSTONE PROJECT: BATTLE OF THE NEIGHBORHOODS
#### 1. Introduction and Business Problem
* A famous fast food chain wants to open a new branch in Toronto.
* The customer requested us to find the best area to place the new store.
* We need to choose a place that has samll number of competitors and high number of potential customers.
* We assume more offices/schools will bring more fast food customers, bacause students tend to like fast food and company employees usually take fast food for lunch. And it is better to choose a place has less fast food restaurants since there will be less competiitors.

#### 2. Data
We need the following data to solve the problem:
* The Neighbourhood/Latitude/Longitude/Postcode data which can be consolidated from:
    * Wikipedia Toronto postcode/neighbourhood data: https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M
    * csv file that has the geographical coordinates of each postal code: http://cocl.us/Geospatial_data
* We will obtain the following venues data from Foursquare :
    * the fast food restaurants in the neighbourhood
    * the high schools in the neighbourhood
    * the universities in the neighbourhood
    * the offices in the neighbourhood
* We will then leverage the data to determine which Neighbourhood is the best location for the new branch.

#### 3. Methodology
* First we retrieves the latitude and longitude of each Postcode of Toronto city, this has been done in the previous week.
* We also collected the venues data of fast food restaurants, high schools, universities and offices in each postcode area from Foursquare.
* Then for each area, we compute the number of fast food restaurants, high schools, universities and offices.
* For each of these four kinds of venues, a weight was assigned based on the top priorities defined by the customer. The weights were set to arbitrary values for this project for simplicity. We can always modify them based on real scenarios.
    * We assiigned weight 1 to High Schools since high school student are potential customers.
    * Weight 2 was assigned for Universities and offiices, since university students and employees are even better potential customers.
    * Fast food restaurants received a negatiive weight (-2), since they are potential competitors .
* Then, the weighted sums of the number of venues was calculated for each of the 4 venue categories (high school, university, office, fast food restaurants).
* At last, we ranked tha areas based on the scores and found the best location for the new fast food branch.

#### 4. Results
##### 4.1 Fast food restaurants in Toronto
![alt text](fastfood.png)

##### 4.2 High schools in Toronto
![alt text](school.png)

##### 4.3 Universities/ Colleges in Toronto
![alt text](university.png)

##### 4.4 Offices in Toronto
![alt text](office.png)

##### 4.4 Ranks and Scores of the postcode areas
The following table shows the top 10 best areas:
![alt text](score.png)

The following map demostrates the scores of all the areas, darker color means higher score. We can notice that the best locations are near Church and Wellesley. This neibourhood is near the University of Toronto and many offices, so it obtained a higher rank. For CBD area, the scores are not very high because there are amny existing fast food chains, so we will face a severe competition if we open a new store at CBD.
![alt text](overview.png)

##### 4.5 A closer look at the best area
Below is the distribution of different kinds of venues at the best area selected. The red circles indicate the potential good locations for the new store, as they are near schools/ offices, and not very close to any competitor. In the plot, red dots indicate existing fast food restaurants, and other color dots indicate a potential source of customer (schools, universities or offices)
![alt text](best.png)

#### 5. Discussions
We may obtain a more accurate estimation of the best location by make the following changes:
* Instead of using postalcode to identify the area, we may also try to use the neighbourhood as well.
* When ranking the areas, we may take more factors into consideration. For example, the population densities, rental cost and average income levels of different areas.

#### 6. Conclusion






